In [1]:
!pip install requests transformers

In [22]:
import requests
import zipfile
import os

# URL du fichier zip sur Hugging Face
zip_url = 'https://huggingface.co/datasets/Dabococo/wheeloh_dataset/images'

# Nom local du fichier zip
zip_file = 'images.zip'

# Télécharger le fichier zip
response = requests.get(zip_url)
content_type = response.headers.get('Content-Type')

# Vérifier que le fichier est un fichier zip
if 'zip' not in content_type:
    raise ValueError("Le fichier téléchargé n'est pas un fichier zip. Content-Type: {}".format(content_type))

# Sauvegarder le contenu téléchargé dans un fichier
with open(zip_file, 'wb') as f:
    f.write(response.content)

# Vérifier la taille du fichier
file_size = os.path.getsize(zip_file)
print("Taille du fichier téléchargé:", file_size, "octets")

# Afficher le début du contenu du fichier pour vérifier
with open(zip_file, 'rb') as f:
    print(f.read(100))  # Lire les 100 premiers octets

# Créer un répertoire pour extraire les fichiers
extract_dir = 'extracted_files'
os.makedirs(extract_dir, exist_ok=True)

# Extraire le contenu du fichier zip
try:
    with zipfile.ZipFile(zip_file, 'r') as zip_ref:
        zip_ref.extractall(extract_dir)
    # Afficher les fichiers extraits
    extracted_files = os.listdir(extract_dir)
    print("Fichiers extraits :", extracted_files)
except zipfile.BadZipFile:
    print("Erreur : le fichier téléchargé n'est pas un fichier zip valide.")

ValueError: Le fichier téléchargé n'est pas un fichier zip. Content-Type: text/html; charset=utf-8

In [7]:
from torchvision.datasets import ImageFolder
import os
from torchvision.datasets.folder import has_file_allowed_extension, IMG_EXTENSIONS, default_loader

class CustomImageFolder(ImageFolder):
    def __init__(self, root, transform=None, loader=default_loader, is_valid_file=None):
        super().__init__(root, transform=transform, loader=loader, is_valid_file=is_valid_file)

    def find_classes(self, directory):
        # Ignorer les répertoires cachés
        classes = [d.name for d in os.scandir(directory) if d.is_dir() and not d.name.startswith('.')]
        classes.sort()
        class_to_idx = {cls_name: i for i, cls_name in enumerate(classes)}
        return classes, class_to_idx

    def make_dataset(self, directory, class_to_idx, extensions=None, is_valid_file=None, allow_empty=False):
        instances = []
        directory = os.path.expanduser(directory)
        both_none = extensions is None and is_valid_file is None
        if both_none:
            raise ValueError("Both extensions and is_valid_file cannot be None")
        if extensions is not None:
            def is_valid_file(x):
                return has_file_allowed_extension(x, extensions)

        for target_class in sorted(class_to_idx.keys()):
            class_index = class_to_idx[target_class]
            target_dir = os.path.join(directory, target_class)
            if not os.path.isdir(target_dir):
                continue
            for root, _, fnames in sorted(os.walk(target_dir)):
                for fname in sorted(fnames):
                    path = os.path.join(root, fname)
                    if is_valid_file(path) and not fname.startswith('.'):
                        item = path, class_index
                        instances.append(item)

        if not allow_empty and len(instances) == 0:
            raise RuntimeError(f"Found 0 files in subfolders of: {directory}. Supported extensions are: {','.join(extensions)}")

        return instances

In [9]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import transforms, models
from tqdm import tqdm

# Configuration
batch_size = 32
num_epochs = 10
learning_rate = 0.001
num_classes = 2

# Préparer les transformations
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Charger les données d'entraînement avec CustomImageFolder
train_dataset = CustomImageFolder(root='/content/dataset/train', transform=transform)
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=4, pin_memory=True)

# Définir le modèle
model = models.resnet18(pretrained=True)
model.fc = nn.Linear(model.fc.in_features, num_classes)
model = model.to('cuda')

# Définir la perte et l'optimiseur
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate)

# Utiliser le scaler pour l'AMP
scaler = torch.cuda.amp.GradScaler()

# Entraînement
for epoch in range(num_epochs):
    model.train()
    running_loss = 0.0
    for inputs, labels in tqdm(train_loader):
        inputs, labels = inputs.to('cuda'), labels.to('cuda')

        # Zero the parameter gradients
        optimizer.zero_grad()

        # Forward pass with autocast
        with torch.cuda.amp.autocast():
            outputs = model(inputs)
            loss = criterion(outputs, labels)

        # Backward pass with scaler
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()

        running_loss += loss.item() * inputs.size(0)

    epoch_loss = running_loss / len(train_loader.dataset)
    print(f'Epoch [{epoch + 1}/{num_epochs}], Loss: {epoch_loss:.4f}')

print('Finished Training')

# Sauvegarder le modèle
torch.save(model.state_dict(), 'model.pth')

100%|██████████| 16/16 [00:08<00:00,  1.86it/s]


Epoch [1/10], Loss: 0.2799


100%|██████████| 16/16 [00:08<00:00,  1.96it/s]


Epoch [2/10], Loss: 0.0916


100%|██████████| 16/16 [00:07<00:00,  2.08it/s]


...

Epoch [8/10], Loss: 0.0101


100%|██████████| 16/16 [00:08<00:00,  1.85it/s]


Epoch [9/10], Loss: 0.0631


100%|██████████| 16/16 [00:07<00:00,  2.20it/s]


Epoch [10/10], Loss: 0.0186
Finished Training


In [ ]:
#Ici pour charger le modèle

In [22]:
import torch
import torch.nn as nn
from torchvision import models, transforms
from PIL import Image

# Définir le modèle
num_classes = 2  # Canard et Perroquet
model = models.resnet18(pretrained=False)
model.fc = nn.Linear(model.fc.in_features, num_classes)
model = model.to('cuda')

# Charger les poids du modèle enregistré
model.load_state_dict(torch.load('model.pth'))
model.eval()  # Mettre le modèle en mode évaluation

# Définir les transformations
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Charger et transformer une nouvelle image
def load_image(image_path):
    image = Image.open(image_path).convert('RGB')
    image = transform(image)
    image = image.unsqueeze(0)  # Ajouter une dimension pour le batch
    return image

# Exemple de chargement d'une image
image_path = '/content/lg.jpeg'
image = load_image(image_path).to('cuda')

# Passer l'image dans le modèle pour obtenir des prédictions
with torch.no_grad():  # Désactiver la grad pour l'inférence
    outputs = model(image)
    _, predicted = torch.max(outputs, 1)

    classes = ['Alpine', 'Bugatti']
    predicted_class = classes[predicted.item()]
    print(f'Predicted class: {predicted_class}')

Predicted class: Bugatti


In [23]:
!pip install transformers huggingface_hub

In [11]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) Y
Token is valid (permission: read).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in c

In [25]:
from huggingface_hub import HfApi, HfFolder, Repository

# Variables
model_path = "Wheeloh-model_1.pth"
repo_name = "Wheeloh-model_1"  # Remplacez par le nom de votre dépôt
commit_message = "Initial commit"

# Se connecter à l'API
api = HfApi()

# Obtenir le token d'authentification
token = HfFolder.get_token()

# Cloner le dépôt Hugging Face
repo_url = api.create_repo(repo_name, token=token, exist_ok=True)
repo = Repository(local_dir=repo_name, clone_from=repo_url)

# Copier le fichier du modèle dans le dépôt local
import shutil
shutil.copy(model_path, repo_name)

# Pousser le modèle sur le hub
repo.push_to_hub(commit_message=commit_message)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message,

Upload file Wheeloh-model_1.pth:   0%|          | 1.00/42.7M [00:00<?, ?B/s]

To https://huggingface.co/Dabococo/Wheeloh-model_1
   09e573f..8606a55  main -> main

   09e573f..8606a55  main -> main



'https://huggingface.co/Dabococo/Wheeloh-model_1/commit/8606a554a318e75a54b8b841b31825c29f577de8'